In [ ]:
import numpy as np
import pandas as pd
import scipy as sp
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import geopandas as gpd
import os


In [5]:
data = pd.read_excel("radio_analogowe_2025-06-09.xlsx")
data.head()

Lp.      Status Numer\npozwolenia\n/decyzji Data\npozwolenia\n/decyzji  \
0    1  Pozwolenie      DC.WRT.5101.321.2019.2                 2019-08-30   
1    2  Pozwolenie      DC.WRT.5101.332.2019.2                 2019-09-06   
2    3  Pozwolenie      DZC.WRT.5101.79.2018.2                 2018-04-18   
3    4  Pozwolenie     DZC.WRT.5101.101.2018.2                 2018-05-22   
4    5  Pozwolenie      DZC.WRT.5101.30.2018.6                 2018-02-14   

    Ważny od   Ważny do                                       Wnioskodawca  \
0 2019-09-09 2028-06-22  Prowincja Warszawska Zgromadzenia Najświętszeg...   
1 2019-09-17 2028-06-22  Prowincja Warszawska Zgromadzenia Najświętszeg...   
2 2018-04-20 2028-04-18                                        EmiTel S.A.   
3 2018-05-26 2028-05-25                                        EmiTel S.A.   
4 2018-02-15 2028-02-14                                        EmiTel S.A.   

                                             Nadawca           Program  \
0  Prowincja Warszawska Zgromadzenia Najświętszeg...      Radio Maryja   
1  Prowincja Warszawska Zgromadzenia Najświętszeg...      Radio Maryja   
2  POLSKIE RADIO - Regionalna Rozgłośnia w Koszal...  Radio Regionalne   
3     Radio Muzyka Fakty Grupa RMF Sp. z o.o. sp. k.            RMF FM   
4                                 Polskie Radio S.A.         Program 2   

   Identyfikator  ...  270° 280° 290° 300° 310° 320° 330° 340° 350°  \
0        1421502  ...     0    0  2,2  2,2    0    0    0    0    0   
1        1421533  ...     0  2,2  2,2  2,2    0    0    0    0    0   
2        1421542  ...     0    0    0    0    0    0    0    0    0   
3        1421551  ...     0    0    0    0    0    0    0    0    0   
4        1421560  ...     0    0    0    0    0    0    0    0    0   

  id wystąpienia  
0        2708967  
1        2710852  
2        2478717  
3        2482008  
4        2462212  

[5 rows x 65 columns]

In [14]:
from pyproj import Transformer
from shapely.geometry import Point
import re
data1 = data[["Program", "Lokalizacja stacji", "F [MHz]", "Dł.geogr.", "Sz.geogr.", "Układ wsp.", "ERP[kW]", "H ant."]].copy()

# --- Krok 1: Konwersja DMS → decimal degrees ---
def dms_to_dd(dms_str):
    match = re.match(r"(\d+)([NSEW])(\d+)'(\d+)?", str(dms_str))
    if not match:
        return None
    deg, dir_, min_, sec = match.groups()
    sec = int(sec) if sec else 0
    dd = int(deg) + int(min_)/60 + sec/3600
    if dir_ in ['S', 'W']:
        dd *= -1
    return round(dd, 6)

# --- Krok 2: Przekształcenie współrzędnych WGS84 ---
mask_wgs = data1["Układ wsp."] == "WGS84"
data1.loc[mask_wgs, "Dl.dd"] = data1.loc[mask_wgs, "Dł.geogr."].apply(lambda x: dms_to_dd(x) if isinstance(x, str) else None)
data1.loc[mask_wgs, "Sz.dd"] = data1.loc[mask_wgs, "Sz.geogr."].apply(lambda x: dms_to_dd(x) if isinstance(x, str) else None)

gdf_wgs = gpd.GeoDataFrame(
    data1.loc[mask_wgs].dropna(subset=["Dl.dd", "Sz.dd"]).copy(),
    geometry = data1.loc[mask_wgs].dropna(subset=["Dl.dd", "Sz.dd"]).apply(lambda r: Point(r["Dl.dd"], r["Sz.dd"]), axis=1),
    crs = "EPSG:4326"
)

# --- Krok 3: Przekształcenie danych z układu 1942 ---
from pyproj import Transformer

mask_1942 = data1["Układ wsp."] == "1942"
data1.loc[mask_1942, "Dl.dd"] = data1.loc[mask_1942, "Dł.geogr."].apply(lambda x: dms_to_dd(x) if isinstance(x, str) else None)
data1.loc[mask_1942, "Sz.dd"] = data1.loc[mask_1942, "Sz.geogr."].apply(lambda x: dms_to_dd(x) if isinstance(x, str) else None)

gdf_1942 = gpd.GeoDataFrame(
    data1.loc[mask_1942].dropna(subset=["Dl.dd", "Sz.dd"]).copy(),
    geometry = data1.loc[mask_1942].dropna(subset=["Dl.dd", "Sz.dd"]).apply(lambda r: Point(r["Dl.dd"], r["Sz.dd"]), axis=1),
    crs = "EPSG:4322"
)
gdf_1942 = gdf_1942.to_crs("EPSG:4326")  # transformacja do WGS84

# --- Krok 4: Połączenie danych ---
gdf_all = pd.concat([gdf_wgs, gdf_1942], ignore_index=True)
gdf_all.to_csv("stacje_radiowe_wszystkie.csv", index=False)
print("✅ Dane zapisane jako: stacje_radiowe_wszystkie.csv")


✅ Dane zapisane jako: stacje_radiowe_wszystkie.csv


In [10]:
gdf_all.head(35)

Program  \
0                                        Radio Maryja   
1                                        Radio Maryja   
2                                    Radio Regionalne   
3                                              RMF FM   
4                                           Program 2   
5                                           Program 3   
6                                           Radio ZET   
7                                           Program 1   
8                                           Program 1   
9                                           Program 3   
10                                    Radio Białystok   
11                                             RMF FM   
12                                             RMF FM   
13                                       Radio Maryja   
14                                       Radio Maryja   
15                                          Radio ZET   
16                                          Radio ZET   
17                                   Radio Regionalne   
18                                             RMF FM   
19                                          Radio ZET   
20                                          Radio ZET   
21  Radio FARA - Rozgłośnia Archidiecezji Przemyskiej   
22                                               PR I   
23                                 Radio Plus Legnica   
24                                       Radio Maryja   
25                                 Radio Plus Legnica   
26                                              PR II   
27                                          Program 2   
28                                       Radio Maryja   
29                                       Radio Maryja   
30                                             RMF FM   
31                                          Radio ZET   
32                                          Radio ZET   
33                                       Radio Maryja   
34                                       Radio Maryja   

                         Lokalizacja stacji  F [MHz]  Dł.geogr.  Sz.geogr.  \
0                                   Lipiany     99.5  14E56'04"  53N01'11"   
1                                  Pełczyce    107.2  15E18'42"  53N02'08"   
2                 RTCN Białogard Sławoborze     92.5  15E40'59"  53N53'05"   
3                      Białogard Sławoborze     96.4  15E41'03"  53N53'08"   
4               78-314 Sławoborze, Trzciana     98.2  15E40'59"  53N53'05"   
5               78-314 Sławoborze, Trzciana    101.5  15E40'59"  53N53'05"   
6                      Białogard Sławoborze    104.2  15E41'03"  53N53'08"   
7               78-314 Sławoborze, Trzciana    106.0  15E40'59"  53N53'05"   
8                         Białystok Krynice     92.3  23E01'28"  53N13'52"   
9                         Białystok Krynice     96.0  23E01'28"  53N13'52"   
10                        Białystok Krynice     99.4  23E01'28"  53N13'52"   
11                        Białystok Krynice    100.2  23E01'28"  53N13'52"   
12                        Białystok Krynice    100.2  23E01'28"  53N13'52"   
13                Białystok, ul. Cieszyńska    104.7  23E08'57"  53N07'38"   
14                        Białystok Krynice    104.7  23E01'28"  53N13'52"   
15                        Białystok Krynice    107.3  23E01'28"  53N13'52"   
16                        Białystok Krynice    107.3  23E01'28"  53N13'52"   
17                            38-612 Solina     99.2  22E29'21"  49N22'58"   
18                      Bieszczady G. Jawor    101.1  22E29'34"  49N23'01"   
19                      Bieszczady G. Jawor    103.1  22E29'34"  49N23'01"   
20                      Bieszczady G. Jawor    103.1  22E29'34"  49N23'01"   
21                    Czarnorzeki k. Krosna    104.5  21E49'58"  49N44'20"   
22                         59-920 Bogatynia     92.8  14E59'25"  50N52'37"   
23                  Łysa Góra k. Dziwiszowa     94.9  15E48'06"  50N57'39"   
24                    Bogatynia Góra Wysoka

In [11]:
import folium
from folium.plugins import MarkerCluster
import math

# Tworzenie mapy
m = folium.Map(location=[52.0, 19.0], zoom_start=6, tiles="CartoDB positron")
cluster = MarkerCluster().add_to(m)

# Konwersja ERP i wysokości anteny
gdf_all["ERP[kW]"] = pd.to_numeric(gdf_all["ERP[kW]"], errors="coerce")
gdf_all["H ant."] = pd.to_numeric(gdf_all["H ant."], errors="coerce")

# Iteracja po danych
for idx, row in gdf_all.iterrows():
    lat, lon = row.geometry.y, row.geometry.x
    erp = row["ERP[kW]"]
    h = row["H ant."]

    popup_text = f"""
    <b>{row['Program']}</b><br>
    Lokalizacja: {row['Lokalizacja stacji']}<br>
    Częstotliwość: {row['F [MHz]']} MHz<br>
    """

    # FeatureGroup łączy popup i zasięg
    group = folium.FeatureGroup()

    # Dodaj znacznik
    marker = folium.Marker(
        location=[lat, lon],
        popup=folium.Popup(popup_text, max_width=300),
        icon=folium.Icon(color="blue", icon="info-sign")
    )
    marker.add_to(group)

    # Dodaj okrąg zasięgu jeśli są dane
    if pd.notnull(erp) and pd.notnull(h) and erp > 0 and h > 0:
        zasieg_km = 3.57 * math.sqrt(erp) * math.sqrt(h)
        folium.Circle(
            location=[lat, lon],
            radius=zasieg_km * 1000,
            color="red",
            fill=True,
            fill_opacity=0.2,
            weight=1,
            popup=f"Szacowany zasięg: {zasieg_km:.1f} km"
        ).add_to(group)

    # Dodaj do klastra
    group.add_to(cluster)

# Wyświetl mapę
m


In [12]:
m.save("mapa_stacji_radiowych.html")
print("✅ Mapa zapisana jako: mapa_stacji_radiowych.html")

✅ Mapa zapisana jako: mapa_stacji_radiowych.html
